# Image processing and feature construction

### **Imports**

In [23]:
# imports

import cv2
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from skimage.feature import local_binary_pattern
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import json
from shapely.geometry import Polygon, box
from shapely.affinity import scale, affine_transform
from collections import Counter
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
import time
from sklearn.metrics import confusion_matrix
import concurrent



### **General functions**

In [2]:
# Function to plot image with given polygons:
def plot_picture_with_polygons(image, polygons):
    fig, ax = plt.subplots(1, figsize=(20,12))
    ax.imshow(image)
    for polygon in polygons:
        points = polygon
        polygon = patches.Polygon(points, closed=True, edgecolor='red', fill=False, linewidth=2, label=label)
        ax.add_patch(polygon)
    plt.show()

# Function to resize the image and its polygons:
def resize_image_and_poylgons(image, defects, upper_pixel_size=1000):

    # Calculate the new widht, heights and the scale factor:
    height, width = image.shape[:2]
    scale_factor = (upper_pixel_size / max(width, height)) if max(width, height) > upper_pixel_size else 1
    new_width, new_height = int(width * scale_factor), int(height * scale_factor)

    # Resize the image:
    resized_image = cv2.resize(image, (new_width, new_height), interpolation=cv2.INTER_AREA)

    # Rescale the defect polygon coordinates:
    rescaled_defects = defects.copy()
    for defect in rescaled_defects:
        defect["points"] = [[x * scale_factor, y * scale_factor] for [x, y] in defect["points"]]

    return resized_image, rescaled_defects

### **Image manipulation functions**

**Texture**

In [3]:
# Function to find rough areas in picture
def rough_image_filter(image, threshold=8):

    #read in image as greyscale
    image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

    #apply local binary pattern
    lbp = local_binary_pattern(image, P=8, R=2, method='uniform')

    lbp_uint8 = np.uint8((lbp / lbp.max())*255)
    
    blurred = cv2.blur(lbp_uint8, (5, 5), 0)
    mean = np.mean(blurred)
    std = np.std(blurred)
    median = np.median(blurred)
    #apply thresholding
    _, binary_image = cv2.threshold(blurred, mean - std, 255, cv2.THRESH_BINARY) 

    binary_blurred = cv2.blur(binary_image, (50, 50), 0)
    mean = np.mean(binary_blurred)
    std = np.std(binary_blurred)
    #apply thresholding
    _, binary_image = cv2.threshold(binary_blurred, mean - 1.5 * std, 255, cv2.THRESH_BINARY) # normlaize and convert to uint8, then blur
    
    return lbp, binary_image

**Color**

In [4]:
# Function to detect color values in an image:
def color_detector(image, lower_bounds: list, upper_bounds: list) -> list:
        
        hsv_image = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
        mask = np.zeros(hsv_image.shape[:2], dtype=np.uint8)
        for lower_bound, upper_bound in zip(lower_bounds, upper_bounds):
            lower_bound = np.array(lower_bound)
            upper_bound = np.array(upper_bound)
            temp_mask = cv2.inRange(hsv_image, lower_bound, upper_bound)
            mask = cv2.bitwise_or(mask, temp_mask)
        return mask

# Function to identify reddish areas in an image: 
def reddish_image_filter(image):

    rusty_lower_bounds = [[0, 40, 50]]
    rusty_upper_bounds = [[20, 255, 200]]
    reddish_areas = color_detector(image, rusty_lower_bounds, rusty_upper_bounds)

    return reddish_areas

# Function to identify metallic areas in an image:
def metallic_image_filter(image):
     
    metallic_lower_bounds = [[90, 5, 120], [20, 10, 150]]
    metallic_upper_bounds = [[120, 60, 240], [130, 60, 220]]
    metallic_areas = color_detector(image, metallic_lower_bounds, metallic_upper_bounds)

    return metallic_areas

# Function to identify colorful areas in an image:
def colorful_image_filter(image):
     
    colorful_lower_bounds = [[0, 60, 50]]
    colorful_upper_bounds = [[180, 255, 255]]
    colorful_areas = color_detector(image, colorful_lower_bounds, colorful_upper_bounds)

    return colorful_areas

# Function to identify black areas in an image:
def black_image_filter(image):
     
    black_lower_bounds = [[0, 0, 0]]
    black_upper_bounds = [[180, 255, 50]]
    black_areas = color_detector(image, black_lower_bounds, black_upper_bounds)

    return black_areas

# Function to create a color bin image filter: 
def color_bins_image_filter(image, bin_size=20):

     # Create a color bin mask:
    color_bin_mask = np.zeros(image.shape[:2], dtype=np.uint8)

    # Create binary color masks for each color space bin:
    for i in range(0, 180, bin_size):
        color_bin_lower_bounds = [[i, 0, 0]]
        color_bin_upper_bounds = [[i + bin_size if i == 180 - bin_size else i + bin_size - 1, 255, 255]]
        color_bin_areas = color_detector(image, color_bin_lower_bounds, color_bin_upper_bounds)
        color_bin_mask[color_bin_areas > 0] = (i // bin_size) + 1

    return color_bin_mask



**Shape**

In [6]:
# Legthy image filter
def lengthy_image_filter(image, ratio = 2.5):
# Blur image:
    gray_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    gray_image = cv2.GaussianBlur(gray_image, (7, 7), 0)

    # Apply edge detector:
    edges = cv2.Canny(gray_image, 50, 150)

    # Apply morphological operations 
    kernel = np.ones((15, 15), np.uint8)
    edges = cv2.dilate(edges, kernel, iterations=1)
    edges = cv2.erode(edges, kernel, iterations=1)

    # Find contours
    contours, _ = cv2.findContours(edges, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    stencil = np.zeros(gray_image.shape).astype(gray_image.dtype)
    color = [255]
    for contour in contours:
        try:
            # Get fitted bounding box
            rect = cv2.minAreaRect(contour)
            box = cv2.boxPoints(rect)
            box = np.int0(box)
            width = rect[1][0]
            height = rect[1][1]
            
            # Calculate aspect ratio
            aspect_ratio = float(max(width, height)) / min(width, height)
            if aspect_ratio > 2.5:
                cv2.drawContours(stencil, [box], 0, (0, 0, 255), 2)
                cv2.fillPoly(stencil, [box], color)
        except:
            pass
    return stencil

In [7]:
# Function to get an image with edges for the lengthy objects filter:
def lengthy_image_filter_edges(image):
    
    # Read in image as greyscale
    gray_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

    # Blur image:
    blurred_image = cv2.GaussianBlur(gray_image, (7, 7), 0)

    # Apply edge detector:
    edges = cv2.Canny(blurred_image, 50, 150)

    # Apply morphological operations 
    kernel = np.ones((15, 15), np.uint8)
    edges = cv2.dilate(edges, kernel, iterations=1)
    edges = cv2.erode(edges, kernel, iterations=1)

    return edges

# Function to get number of contours with aspect ratio > 2:
def extract_lengthy_features_1(edges, defect_polygon):

    # Create defect polygon and calculate its width and height:
    defect_polygon = Polygon(defect_polygon)
    defect_rect_coords = np.array(list(defect_polygon.minimum_rotated_rectangle.exterior.coords)[:-1])
    distances = [np.linalg.norm(defect_rect_coords[i] - defect_rect_coords[(i + 1) % len(defect_rect_coords)]) for i in range(len(defect_rect_coords))]
    defect_width, defect_height = sorted(distances)[0], sorted(distances)[-1]

    # Find contours
    contours, _ = cv2.findContours(edges, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    # Extract overlapping contours (where >80% of the contour area is overlapping with the polygon):
    overlapping_contours = []
    for contour in contours: 
        if not np.array_equal(contour[0], contour[-1]):
            contour = np.vstack([contour, contour[0:1]])
        try:
            contour_as_polygon = Polygon([(x, y) for x, y in contour[:, 0]])
            intersection = contour_as_polygon.intersection(defect_polygon)
            intersection_area = intersection.area
        except:
            intersection_area = 0
        contour_area = contour_as_polygon.area
        if intersection_area > 0 and intersection_area >= 0.8 * contour_area:
            overlapping_contours.append(contour)

    # Extract characteristics per overlapping contour:
    characteristics = []
    lengths = []
    for contour in overlapping_contours:

        # Get fitted bounding box
        rect = cv2.minAreaRect(contour)
        box = cv2.boxPoints(rect)
        box = np.int0(box)
        width = max(rect[1][0], 1)
        height = max(rect[1][1], 1)
        
        # Calculate aspect ratio
        aspect_ratio = float(max(width, height) / min(width, height))
        characteristics.append(aspect_ratio)
        lengths.append(max(width, height))
    
    # Extract number of contours with aspect ratio >= 2 and the average aspect ratio of these contours:
    number = 0
    avg_aspect_ratio_lengthy = 0
    for aspect_ratio in characteristics:
        if aspect_ratio >= 2.5:
            avg_aspect_ratio_lengthy += aspect_ratio
            number += 1
    avg_aspect_ratio_lengthy = max(avg_aspect_ratio_lengthy / max(number, 1), 1)

    # Extract the quotient (length of the lengthiest contour) / (length of the defect):
    rel_length = (max(lengths) / max(defect_width, defect_height)) if len(lengths) > 0 else 0

    return number, avg_aspect_ratio_lengthy, rel_length


In [8]:
# Function to get a filtered image with the convex hulls of connected edges:
def convex_shape_image_filter(image):

    # Convert image to greyscale:
    image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

    # Blur image:
    image = cv2.GaussianBlur(image, (5, 5), 2)

    # Apply morphological operations: 
    edges = cv2.Canny(image, 50, 150)
    kernel = np.ones((10, 10), np.uint8)
    edges = cv2.dilate(edges, kernel, iterations=1)
    kernel = np.ones((8, 8), np.uint8)
    edges = cv2.erode(edges, kernel, iterations=1)
    
    # Create a mask which fills the convex hulls of connected edges and create a list with all convex hulls:
    contours, _ = cv2.findContours(edges, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    mask = np.zeros_like(edges, dtype=np.uint8)
    hulls = []
    for contour in contours:
        hull = cv2.convexHull(contour)
        hulls.append(hull)
        cv2.drawContours(mask, [hull], -1, (255), thickness=cv2.FILLED)
    
    # Create a new binary image with the convex hulls:
    filled_edges = cv2.bitwise_or(edges, mask)

    return filled_edges, contours, hulls

**Pixel intensities**

In [9]:
# Find darker areas in an image
def darker_image_filter(image, z = 200):
    # Convert image to grayscale:
    grey_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    grey_image = cv2.blur(grey_image, (15, 15), 0)
    mean = np.mean(grey_image)
    std = np.std(grey_image) / 250
    dark_areas = (grey_image < mean - z * std)
    dark_areas = dark_areas.astype(np.uint8)
    blurred = cv2.blur(dark_areas, (5, 5), 0) *255
    return blurred

### **Feature calculation functions**

**General functions**

In [10]:
def get_overlapping_values(filtered_image, defect_polygon):
    # Generate polygon mask:
    mask = np.zeros(filtered_image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask, [defect_polygon], 255)

    # Extract overlapping pixel values:
    overlapping_values = filtered_image[mask == 255]
    overlapping_values = overlapping_values.tolist()
    
    return overlapping_values

def get_relative_frequencies(values: list) -> dict:
    
    counts = Counter(values)
    total_count = len(values)
    relative_frequencies = {element: count / total_count for element, count in counts.items()}
    return relative_frequencies

**Texture**

In [11]:
def extract_rough_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    try:
        quotient = relative_frequencies[0]
    except:
        quotient = 0
    return quotient

def extract_rough_features_1(lbp_image, defect_polygon):

    overlapping_values = get_overlapping_values(lbp_image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    
    lbp_value_quotients = []
    entropy = 0
    for i in range(10):
        lbp_value_quotients.append(relative_frequencies[i] if i in relative_frequencies else 0)
        entropy -= lbp_value_quotients[i] * (np.log2(lbp_value_quotients[i]) if lbp_value_quotients[i] != 0 else 0)
    most_frequent_lbp_value = lbp_value_quotients.index(max(lbp_value_quotients))

    return most_frequent_lbp_value, lbp_value_quotients, entropy

**Color**

In [12]:
def extract_reddish_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    try:
        quotient = relative_frequencies[255]
    except:
        quotient = 0
    return quotient

def extract_metallic_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    quotient = relative_frequencies[255] if 255 in relative_frequencies else 0

    return quotient

def extract_colorful_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    quotient = relative_frequencies[255] if 255 in relative_frequencies else 0

    return quotient

def extract_black_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    quotient = relative_frequencies[255] if 255 in relative_frequencies else 0

    return quotient

def extract_black_thin_feature(image, defect_polygon):

    # Construct strengthened image:
    kernel = np.ones((20, 20), np.uint8)
    strengthened_image = cv2.dilate(image, kernel, iterations=1)
    difference_image = np.where((strengthened_image == 255) & (image == 0), 255, 0).astype(np.uint8)

    overlapping_values = get_overlapping_values(difference_image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    quotient = relative_frequencies[255] if 255 in relative_frequencies else 0

    return quotient

def extract_color_features_1(color_bins_image, defect_polygon, bin_size=20):

    overlapping_values = get_overlapping_values(color_bins_image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    
    color_bin_quotients = []
    entropy = 0
    for i in range(int(180 / bin_size)):
        color_bin_quotients.append(relative_frequencies[i + 1] if i + 1 in relative_frequencies else 0)
        entropy -= color_bin_quotients[i] * (np.log2(color_bin_quotients[i]) if color_bin_quotients[i] != 0 else 0)
    most_frequent_color_bin = color_bin_quotients.index(max(color_bin_quotients)) + 1

    return most_frequent_color_bin, color_bin_quotients, entropy



**Shapes**

In [13]:
def extract_lengthy_feature(image, defect_polygon):
    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    try:
        quotient = relative_frequencies[255]
    except:
        quotient = 0
    return quotient

In [14]:
def extract_in_shape_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    quotient = relative_frequencies[255] if 255 in relative_frequencies else 0

    return quotient

def extract_roundness_feature(image, hulls, defect_polygon):

    # Function to calculate the roundness value of the convex hull of a shape:
    def roundness(hull):

        area = cv2.contourArea(hull)
        perimeter = cv2.arcLength(hull, True)
        roundness_value = (4 * np.pi * area) / (perimeter ** 2)
        
        return roundness_value
    
    # Calculate roundness values for each convex hull:
    roundnesses = []
    for hull in hulls:
        roundnesses.append(roundness(hull))

    # Create a mask for the defect polygon:
    mask_defect_polygon = np.zeros(image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask_defect_polygon, [defect_polygon], 1)

    # Get intersection area between the defect polygon and each convex hull:
    intersection_areas = []
    defect_polygon_p = Polygon(defect_polygon)
    for hull in hulls:
        hull_polygon = Polygon(hull.reshape(-1, 2))
        if defect_polygon_p.intersects(hull_polygon):
            try:
                if defect_polygon_p.intersection(hull_polygon).area > 0.1 * defect_polygon_p.area:
                    mask_hull = np.zeros_like(image, dtype=np.uint8)
                    cv2.fillConvexPoly(mask_hull, hull, 1)
                    intersection = cv2.bitwise_and(mask_hull, mask_defect_polygon)
                    intersection_areas.append(np.sum(intersection))
                else:
                    intersection_areas.append(0)
            except:
                intersection_areas.append(0)
        else:
            intersection_areas.append(0)

    # Calculate the average roundness value of the convex shapes overlapping with the defect polygon:
    total_intersection_area = sum(intersection_areas)
    weights = [(intersection_area / total_intersection_area if total_intersection_area > 0 else 0) 
               for intersection_area in intersection_areas]
    roundness_value = np.dot(weights, roundnesses)

    return roundness_value


In [15]:
def extract_hu_moments_features(image, contours, defect_polygon):
    
    # Calculate hu moments for each contour:
    hu_moments = []
    for contour in contours:
        moments = cv2.moments(contour)
        hu_moments_contour = cv2.HuMoments(moments).flatten()
        hu_moments.append(hu_moments_contour)
    hu_moments = [list(i) for i in zip(*hu_moments)]

    # Create a mask for the defect polygon:
    mask_defect_polygon = np.zeros(image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask_defect_polygon, [defect_polygon], 1)

    # Get intersection area between the defect polygon and each contour:
    intersection_areas = []
    defect_polygon_p = Polygon(defect_polygon)
    for contour in contours:
        contour_polygon = Polygon(contour.reshape(-1, 2))
        if defect_polygon_p.intersects(contour_polygon):
            try:
                if (defect_polygon_p.intersection(contour_polygon).area > 0.1 * defect_polygon_p.area and 
                    defect_polygon_p.intersection(contour_polygon).area > 0.1 * contour_polygon.area):
                    mask_contour = np.zeros_like(image, dtype=np.uint8)
                    cv2.fillConvexPoly(mask_contour, contour, 1)
                    intersection = cv2.bitwise_and(mask_contour, mask_defect_polygon)
                    intersection_areas.append(np.sum(intersection))
                else:
                    intersection_areas.append(0)
            except:
                intersection_areas.append(0)
        else:
            intersection_areas.append(0)

    # Calculate the average hu moments for of each contour overlapping with the defect polygon:
    total_intersection_area = sum(intersection_areas)
    weights = [(intersection_area / total_intersection_area if total_intersection_area > 0 else 0) 
               for intersection_area in intersection_areas]
    hu_moments_polygon = []
    for hu_moment in hu_moments:
        hu_moments_polygon.append(np.dot(weights, hu_moment))

    return hu_moments_polygon

**Pixel intensities**

In [16]:
def extract_dark_feature(image, defect_polygon):

    overlapping_values = get_overlapping_values(image, defect_polygon)
    relative_frequencies = get_relative_frequencies(overlapping_values)
    try:
        quotient = relative_frequencies[255]
    except:
        quotient = 0
    return quotient

In [17]:
def scale_polygon(polygon, scale):
    # Calculate the centroid of the polygon
    centroid = np.mean(polygon, axis=0)
    
    # Scale the polygon coordinates
    scaled_polygon = (polygon - centroid) * scale + centroid
    return scaled_polygon.astype(np.int32)

def calculate_average_darkness(image, mask):
    # Calculate the average darkness in the masked area
    masked_image = cv2.bitwise_and(image, image, mask=mask)
    gray_image = cv2.cvtColor(masked_image, cv2.COLOR_BGR2GRAY)
    values = gray_image[mask > 0]
    average = np.mean(values)
    return average

def darkness_gradient(image, polygon, scale_outer = 0.85, scale_inner = 0.7):

    # Convert the polygon to np.int32
    original_polygon = np.array(polygon, dtype=np.int32)
    
    # Create a polygon that is 1.1 times the size of the original polygon
    outer_polygon = scale_polygon(original_polygon, scale_outer)
    inner_polygon = scale_polygon(original_polygon, scale_inner)
    
    # Reshape the polygons to the required format
    original_polygon = original_polygon.reshape((-1, 1, 2))
    outer_polygon = outer_polygon.reshape((-1, 1, 2))
    inner_polygon = inner_polygon.reshape((-1, 1, 2))
    
    # Create a mask for the area between the polygons
    mask_outer = np.zeros(image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask_outer, [original_polygon], 255)
    cv2.fillPoly(mask_outer, [outer_polygon], 0)

    mask_inner = np.zeros(image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask_inner, [outer_polygon], 255)
    cv2.fillPoly(mask_inner, [inner_polygon], 0)
    
    average_darkness_outer = calculate_average_darkness(image, mask_outer)
    average_darkness_inner = calculate_average_darkness(image, mask_inner)

    feature_value = average_darkness_inner / average_darkness_outer
    return feature_value

### **Dataset construction**

In [20]:
class Dataset():

    def __init__(self, dataset_type, features_list, images, annotations, data):
        
        self.dataset_type = dataset_type
        self.features_list = features_list
        self.images = images
        self.annotations = annotations
        self.data = data

    class DatasetGenerator():

        def __init__(self, dataset_type, features_list, parameter_list):
            
            self.features_list = features_list
            self.dataset_type = dataset_type
            self.parameter_list = parameter_list

        def build(self, images, annotations):

            return self.process_images_parallel(images, annotations)
            #return self.process_images(images, annotations)
        
        def process_images_parallel(self, images, annotations):

            samples = []

            indices = [str(i).zfill(4) for i, _ in enumerate(images)]
            images_annotations = list(zip(images, annotations, indices))

            with concurrent.futures.ProcessPoolExecutor() as executor:
                futures = {executor.submit(self.create_samples, image_annotations): image_annotations for image_annotations in images_annotations}

            for future in concurrent.futures.as_completed(futures):
                samples_image = future.result()
                samples.extend(samples_image)

            samples = pd.DataFrame(samples)
            return samples
        
        def process_images(self, images, annotations):

            samples = []

            for i, image in enumerate(images):
                image_annotations = (image, annotations[i], str(i).zfill(4))
                samples.extend(self.create_samples(image_annotations))

            samples = pd.DataFrame(samples)
            return samples
            
        def create_samples(self, image_annotations):

            image = image_annotations[0]
            defects = image_annotations[1]
            image_number = image_annotations[2]

            samples = []

            # Manipulate image
            darker_image = darker_image_filter(image)
            reddish_image = reddish_image_filter(image)
            metallic_image = metallic_image_filter(image)
            colorful_image = colorful_image_filter(image)
            black_image = black_image_filter(image)
            color_bins_image = color_bins_image_filter(image, bin_size=20)
            lbp_image, rough_image = rough_image_filter(image)
            lengthy_image = lengthy_image_filter(image)
            edges_for_lengthy_feature = lengthy_image_filter_edges(image)
            convex_shapes_image, contours, hulls = convex_shape_image_filter(image)

            for k in range(len(defects)):
                label = defects[k]['label']
                try:
                    defect_polygon = np.array(defects[k]['points'], dtype = np.int32)
                    gradient_feature = darkness_gradient(image, defects[k]['points'])
                    darker_quotient = extract_dark_feature(darker_image, defect_polygon)
                    reddish_quotient = extract_reddish_feature(reddish_image, defect_polygon)
                    metallic_quotient = extract_metallic_feature(metallic_image, defect_polygon)
                    colorful_quotient = extract_colorful_feature(colorful_image, defect_polygon)
                    black_quotient = extract_black_feature(black_image, defect_polygon)
                    black_thin_quotient = extract_black_thin_feature(black_image, defect_polygon)
                    black_thin_proportion = (black_thin_quotient - black_quotient)
                    dominating_color, color_bin_quotients, color_entropy = extract_color_features_1(color_bins_image, defect_polygon, bin_size=20)
                    rough_quotient = extract_rough_feature(rough_image, defect_polygon)
                    dominating_texture, lbp_value_quotients, texture_entropy = extract_rough_features_1(lbp_image, defect_polygon)
                    lengthy_quotient = extract_lengthy_feature(lengthy_image, defect_polygon)
                    number_lengthy_objects, avg_aspect_ratio, rel_length = extract_lengthy_features_1(edges_for_lengthy_feature, defect_polygon)
                    in_shape_quotient = extract_in_shape_feature(convex_shapes_image, defect_polygon)
                    roundness_value = extract_roundness_feature(convex_shapes_image, hulls, defect_polygon) 
                    hu_moments = extract_hu_moments_features(convex_shapes_image, contours, defect_polygon)

                    temp_dict = {'image_number': image_number, 'defect_number': k, 'label': label,
                                'darker': darker_quotient, 'gradient': gradient_feature, 'reddish': reddish_quotient, 'metallic': metallic_quotient, 
                                'colorful': colorful_quotient,
                                'black': black_quotient, 'black_thin': black_thin_proportion, "dominating_color": dominating_color, 
                                'color_bin_1': color_bin_quotients[0], 'color_bin_2': color_bin_quotients[1],'color_bin_3': color_bin_quotients[2],
                                'color_bin_4': color_bin_quotients[3], 'color_bin_5': color_bin_quotients[4], 'color_bin_6': color_bin_quotients[5],
                                'color_bin_7': color_bin_quotients[6], 'color_bin_8': color_bin_quotients[7], 'color_bin_9': color_bin_quotients[8],
                                "color_entropy": color_entropy,
                                'rough': rough_quotient, 'dominating_texture': dominating_texture, 'texture_0': lbp_value_quotients[0], 
                                'texture_1': lbp_value_quotients[1], 'texture_2': lbp_value_quotients[2], 'texture_3': lbp_value_quotients[3], 
                                'texture_4': lbp_value_quotients[4], 'texture_5': lbp_value_quotients[5], 'texture_6': lbp_value_quotients[6], 
                                'texture_7': lbp_value_quotients[7], 'texture_8': lbp_value_quotients[8], 'texture_9': lbp_value_quotients[9], 
                                'rough_entropy': texture_entropy,
                                'lengthy': lengthy_quotient, 'number_lengthy_objects': number_lengthy_objects, 'lengthy_aspect_ratio': avg_aspect_ratio, 
                                'rel_length': rel_length, 'in_shape': in_shape_quotient, 'roundness': roundness_value,
                                'hu_moment_1': hu_moments[0], 'hu_moment_2': hu_moments[1], 'hu_moment_3': hu_moments[2], 'hu_moment_4': hu_moments[3],
                                'hu_moment_5': hu_moments[4], 'hu_moment_6': hu_moments[5], 'hu_moment_7': hu_moments[6]}
                    samples.append(temp_dict)
                except:
                    pass

            return samples

        
        def read_in_data(self, start, end):

            images_list = []
            annotations_list = []

            for i in range(start, end):

                i = str(i).zfill(4)
                
                image_path = f"data/dacl10k_v2_devphase/images/{self.dataset_type}/dacl10k_v2_{self.dataset_type}_{i}.jpg"
                image = cv2.imread(image_path, cv2.IMREAD_COLOR)

                annotations_path = f"data/dacl10k_v2_devphase/annotations/{self.dataset_type}/dacl10k_v2_{self.dataset_type}_{i}.json"
                with open(annotations_path, 'r') as file:
                    annotations = json.load(file)
                defects = annotations['shapes']

                image, defects = resize_image_and_poylgons(image, defects, 1000)

                images_list.append(image)
                annotations_list.append(defects)

            return images_list, annotations_list
        
            

    @classmethod
    def new(cls, dataset_type, features_list, parameter_list):

        start = 0
        end = 6935 if dataset_type == "train" else 975
        end = 100

        builder = cls.DatasetGenerator(dataset_type, features_list, parameter_list)
        images, annotations = builder.read_in_data(start, end)
        data = builder.build(images, annotations)

        return cls(dataset_type, features_list, images, annotations, data)
    
    def regenerate(self, parameter_list):

        builder = self.DatasetGenerator(self.dataset_type, self.features_list, parameter_list)
        self.data = builder.build(self.images, self.annotations)


In [20]:
class Dataset():

    def __init__(self, dataset_type, features_list, images, annotations, data):
        
        self.dataset_type = dataset_type
        self.features_list = features_list
        self.images = images
        self.annotations = annotations
        self.data = data

    class DatasetGenerator():

        def __init__(self, images, annotations, features_list, parameter_list):
            
            self.images = images
            self.annotations = annotations
            self.features_list = features_list
            self.parameter_list = parameter_list

        def build(self):

            #return self.process_images_parallel()
            return self.process_images()
        
        def process_images_parallel(self):

            samples = []
            image_numbers = [i for i, _ in enumerate(self.images)]

            with concurrent.futures.ProcessPoolExecutor() as executor:
                futures = {executor.submit(self.create_samples, image_number): image_number for image_number in image_numbers}
            
            for future in concurrent.futures.as_completed(futures):
                samples_image = future.result()
                samples.extend(samples_image)

            samples = pd.DataFrame(samples)
            return samples
        
        def process_images(self):

            samples = []

            for i, _ in enumerate(self.images):
                samples.extend(self.create_samples(i))

            samples = pd.DataFrame(samples)
            return samples
            
        def create_samples(self, image_number):

            image = self.images[image_number]
            defects = self.annotations[image_number]

            samples = []

            # Manipulate image
            darker_image = darker_image_filter(image)
            reddish_image = reddish_image_filter(image)
            metallic_image = metallic_image_filter(image)
            colorful_image = colorful_image_filter(image)
            black_image = black_image_filter(image)
            color_bins_image = color_bins_image_filter(image, bin_size=20)
            lbp_image, rough_image = rough_image_filter(image)
            lengthy_image = lengthy_image_filter(image)
            edges_for_lengthy_feature = lengthy_image_filter_edges(image)
            convex_shapes_image, contours, hulls = convex_shape_image_filter(image)

            for k in range(len(defects)):
                label = defects[k]['label']
                try:
                    defect_polygon = np.array(defects[k]['points'], dtype = np.int32)
                    gradient_feature = darkness_gradient(image, defects[k]['points'])
                    darker_quotient = extract_dark_feature(darker_image, defect_polygon)
                    reddish_quotient = extract_reddish_feature(reddish_image, defect_polygon)
                    metallic_quotient = extract_metallic_feature(metallic_image, defect_polygon)
                    colorful_quotient = extract_colorful_feature(colorful_image, defect_polygon)
                    black_quotient = extract_black_feature(black_image, defect_polygon)
                    black_thin_quotient = extract_black_thin_feature(black_image, defect_polygon)
                    black_thin_proportion = (black_thin_quotient - black_quotient)
                    dominating_color, color_bin_quotients, color_entropy = extract_color_features_1(color_bins_image, defect_polygon, bin_size=20)
                    rough_quotient = extract_rough_feature(rough_image, defect_polygon)
                    dominating_texture, lbp_value_quotients, texture_entropy = extract_rough_features_1(lbp_image, defect_polygon)
                    lengthy_quotient = extract_lengthy_feature(lengthy_image, defect_polygon)
                    number_lengthy_objects, avg_aspect_ratio, rel_length = extract_lengthy_features_1(edges_for_lengthy_feature, defect_polygon)
                    in_shape_quotient = extract_in_shape_feature(convex_shapes_image, defect_polygon)
                    roundness_value = extract_roundness_feature(convex_shapes_image, hulls, defect_polygon) 
                    hu_moments = extract_hu_moments_features(convex_shapes_image, contours, defect_polygon)

                    temp_dict = {'image_number': str(image_number).zfill(4), 'defect_number': k, 'label': label,
                                'darker': darker_quotient, 'gradient': gradient_feature, 'reddish': reddish_quotient, 'metallic': metallic_quotient, 
                                'colorful': colorful_quotient,
                                'black': black_quotient, 'black_thin': black_thin_proportion, "dominating_color": dominating_color, 
                                'color_bin_1': color_bin_quotients[0], 'color_bin_2': color_bin_quotients[1],'color_bin_3': color_bin_quotients[2],
                                'color_bin_4': color_bin_quotients[3], 'color_bin_5': color_bin_quotients[4], 'color_bin_6': color_bin_quotients[5],
                                'color_bin_7': color_bin_quotients[6], 'color_bin_8': color_bin_quotients[7], 'color_bin_9': color_bin_quotients[8],
                                "color_entropy": color_entropy,
                                'rough': rough_quotient, 'dominating_texture': dominating_texture, 'texture_0': lbp_value_quotients[0], 
                                'texture_1': lbp_value_quotients[1], 'texture_2': lbp_value_quotients[2], 'texture_3': lbp_value_quotients[3], 
                                'texture_4': lbp_value_quotients[4], 'texture_5': lbp_value_quotients[5], 'texture_6': lbp_value_quotients[6], 
                                'texture_7': lbp_value_quotients[7], 'texture_8': lbp_value_quotients[8], 'texture_9': lbp_value_quotients[9], 
                                'rough_entropy': texture_entropy,
                                'lengthy': lengthy_quotient, 'number_lengthy_objects': number_lengthy_objects, 'lengthy_aspect_ratio': avg_aspect_ratio, 
                                'rel_length': rel_length, 'in_shape': in_shape_quotient, 'roundness': roundness_value,
                                'hu_moment_1': hu_moments[0], 'hu_moment_2': hu_moments[1], 'hu_moment_3': hu_moments[2], 'hu_moment_4': hu_moments[3],
                                'hu_moment_5': hu_moments[4], 'hu_moment_6': hu_moments[5], 'hu_moment_7': hu_moments[6]}
                    samples.append(temp_dict)
                except:
                    pass

            return samples

    @staticmethod    
    def read_in_data(dataset_type, start, end):

        images_list = []
        annotations_list = []

        for i in range(start, end):

            i = str(i).zfill(4)
            
            image_path = f"../data/dacl10k_v2_devphase/images/{dataset_type}/dacl10k_v2_{dataset_type}_{i}.jpg"
            image = cv2.imread(image_path, cv2.IMREAD_COLOR)

            annotations_path = f"../data/dacl10k_v2_devphase/annotations/{dataset_type}/dacl10k_v2_{dataset_type}_{i}.json"
            with open(annotations_path, 'r') as file:
                annotations = json.load(file)
            defects = annotations['shapes']

            image, defects = resize_image_and_poylgons(image, defects, 1000)

            images_list.append(image)
            annotations_list.append(defects)

        return images_list, annotations_list
        
    @classmethod
    def new(cls, dataset_type, features_list, parameter_list):

        start = 0
        end = 6935 if dataset_type == "train" else 975
        end = 100

        images, annotations = cls.read_in_data(dataset_type, start, end)
        builder = cls.DatasetGenerator(images, annotations, features_list, parameter_list)
        data = builder.build()

        return cls(dataset_type, features_list, images, annotations, data)
    
    def regenerate(self, parameter_list):

        builder = self.DatasetGenerator(self.images, self.annotations, self.dataset_type, self.features_list, parameter_list)
        self.data = builder.build(self.images, self.annotations)

    def save_to_csv(self):

        self.data.to_csv(f"{self.dataset_type}_samples_all_defects.csv")


In [21]:
features_list = ["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", 
                 "color_bin_2", "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", 
                 "color_entropy", "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", 
                 "texture_5", "texture_6", "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", 
                 "lengthy_aspect_ratio", "rel_length", "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", 
                 "hu_moment_4", "hu_moment_5", "hu_moment_6", "hu_moment_7"]

train_dataset = Dataset.new(dataset_type="train", features_list=features_list, parameter_list=None)
train_dataset.data





C:\Users\koeni\AppData\Local\Temp\ipykernel_56096\1559176094.py:25: DeprecationWarning: `np.int0` is a deprecated alias for `np.intp`.  (Deprecated NumPy 1.24)
  box = np.int0(box)
C:\Users\koeni\AppData\Local\Temp\ipykernel_56096\2386869206.py:55: DeprecationWarning: `np.int0` is a deprecated alias for `np.intp`.  (Deprecated NumPy 1.24)
  box = np.int0(box)
c:\Users\koeni\Documents\Programme\Python_3.11\Lib\site-packages\numpy\core\fromnumeric.py:3464: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
c:\Users\koeni\Documents\Programme\Python_3.11\Lib\site-packages\numpy\core\_methods.py:192: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


image_number  defect_number          label    darker  gradient   reddish   
0           0000              0       Graffiti  0.184720  0.980610  0.000067  \
1           0000              1       Graffiti  0.023357  0.927555  0.000000   
2           0001              0       Graffiti  0.186930  0.975594  0.205754   
3           0001              1       Drainage  1.000000  0.764369  0.002554   
4           0001              2       Drainage  1.000000  0.860734  0.000000   
..           ...            ...            ...       ...       ...       ...   
844         0099              0   Restformwork  0.732352  1.114840  0.000513   
845         0099              1           Rust  0.415871  0.954652  0.631341   
846         0099              2  Efflorescence  0.000000  1.040908  0.000000   
847         0099              3          Crack  0.074615  1.079748  0.004683   
848         0099              4       Spalling  0.000000  0.967633  0.000000   

     metallic  colorful     black  black_thin  ...  rel_length  in_shape   
0    0.406485  0.112131  0.100255    0.480339  ...    1.114907  0.940367  \
1    0.505482  0.082784  0.022166    0.240129  ...    0.975326  0.664058   
2    0.359605  0.286188  0.006491    0.003690  ...    0.412051  0.153030   
3    0.004839  0.018011  0.839247   -0.678495  ...    0.000000  0.928495   
4    0.004118  0.021153  0.535380   -0.146387  ...    0.000000  0.883564   
..        ...       ...       ...         ...  ...         ...       ...   
844  0.079395  0.010245  0.138421    0.337947  ...    0.355970  0.455535   
845  0.001005  0.443998  0.000000    0.000000  ...    0.000000  0.155198   
846  0.306117  0.000000  0.000000    0.000000  ...    0.414332  0.287793   
847  0.063026  0.000159  0.031275    0.062232  ...    0.873610  0.628354   
848  0.141791  0.000000  0.000000    0.000000  ...    0.019271  0.037151   

     roundness  hu_moment_1  hu_moment_2  hu_moment_3  hu_moment_4   
0     0.753179     0.569272     0.121235     0.076908     0.012198  \
1     0.464764     1.029361     0.991303     2.576770     2.320157   
2     0.000000     0.000000     0.000000     0.000000     0.000000   
3     0.759246     3.488408     1.374017    45.187611     7.360193   
4     0.782024     0.000000     0.000000     0.000000     0.000000   
..         ...          ...          ...          ...          ...   
844   0.371191     0.000000     0.000000     0.000000     0.000000   
845   0.292294     0.000000     0.000000     0.000000     0.000000   
846   0.716414     0.348456     0.061046     0.013709     0.006145   
847   0.199240     5.706277    31.951978     2.123998     0.487655   
848   0.000000     0.000000     0.000000     0.000000     0.000000   

     hu_moment_5  hu_moment_6  hu_moment_7  
0      -0.000039    -0.004143    -0.000372  
1       9.157757     2.799025    -0.132718  
2       0.000000     0.000000     0.000000  
3    -115.506591    -6.730472   -68.377017  
4       0.000000     0.000000     0.000000  
..           ...          ...          ...  
844     0.000000     0.000000     0.000000  
845     0.000000     0.000000     0.000000  
846     0.000055     0.000992     0.000015  
847     0.305641     0.444539    -0.391022  
848     0.000000     0.000000     0.000000  

[849 rows x 47 columns]

In [19]:
a = Dataset.DatasetGenerator("train", None, None)
a.read_in_data(start=0, end=6935)


([array([[[ 47,  63,  52],
          [ 47,  61,  50],
          [ 42,  56,  45],
          ...,
          [187, 178, 174],
          [188, 179, 175],
          [191, 182, 178]],
  
         [[ 37,  53,  42],
          [ 37,  53,  42],
          [ 45,  59,  48],
          ...,
          [189, 180, 176],
          [191, 182, 178],
          [194, 185, 181]],
  
         [[ 40,  56,  45],
          [ 33,  49,  38],
          [ 40,  55,  44],
          ...,
          [191, 182, 178],
          [195, 186, 182],
          [199, 190, 186]],
  
         ...,
  
         [[  4,   3,   7],
          [  5,   4,   8],
          [  5,   4,   8],
          ...,
          [  7,   0,   7],
          [  8,   1,   8],
          [  9,   2,   9]],
  
         [[  6,   5,   9],
          [  5,   4,   8],
          [  8,   7,  11],
          ...,
          [  7,   0,   7],
          [  8,   1,   8],
          [  9,   2,   9]],
  
         [[  3,   3,   6],
          [  2,   2,   5],
          [  7,   6,  10

In [17]:
start = 0
end = 6935
samples = []
no_defects = 0

for i in range(start, end):
    i = str(i).zfill(4)
    if int(i) % 10 == 0:
        print()
        print(f"Processing image {i}")

    #Bild einlesen
    image_path = f"data/dacl10k_v2_devphase/images/train/dacl10k_v2_train_{i}.jpg"
    image = cv2.imread(image_path, cv2.IMREAD_COLOR)

    #Defekte einlesen
    annotations_path = f"data/dacl10k_v2_devphase/annotations/train/dacl10k_v2_train_{i}.json"
    with open(annotations_path, 'r') as file:
        annotations = json.load(file)
    defects = annotations['shapes']

    # Bild und Defekte skalieren
    image, defects = resize_image_and_poylgons(image, defects, 1000)

    #Areas finden
    darker_image = darker_image_filter(image)
    reddish_image = reddish_image_filter(image)
    metallic_image = metallic_image_filter(image)
    colorful_image = colorful_image_filter(image)
    black_image = black_image_filter(image)
    color_bins_image = color_bins_image_filter(image, bin_size=20)
    lbp_image, rough_image = rough_image_filter(image)
    lengthy_image = lengthy_image_filter(image)
    edges_for_lengthy_feature = lengthy_image_filter_edges(image)
    #circles = extract_circles(image)
    convex_shapes_image, contours, hulls = convex_shape_image_filter(image)

    for k in range(len(defects)):
        label = defects[k]['label']
        #if label in ["Rust", "Graffiti", "Drainage", "Wetspot", "ExposedRebars", "Crack"]:
        if True:
            try:
                no_defects += 1
                defect_polygon = np.array(defects[k]['points'], dtype = np.int32)
                gradient_feature = darkness_gradient(image, defects[k]['points'])
                darker_quotient = extract_dark_feature(darker_image, defect_polygon)
                reddish_quotient = extract_reddish_feature(reddish_image, defect_polygon)
                metallic_quotient = extract_metallic_feature(metallic_image, defect_polygon)
                colorful_quotient = extract_colorful_feature(colorful_image, defect_polygon)
                black_quotient = extract_black_feature(black_image, defect_polygon)
                black_thin_quotient = extract_black_thin_feature(black_image, defect_polygon)
                black_thin_proportion = (black_thin_quotient - black_quotient)
                dominating_color, color_bin_quotients, color_entropy = extract_color_features_1(color_bins_image, defect_polygon, bin_size=20)
                rough_quotient = extract_rough_feature(rough_image, defect_polygon)
                dominating_texture, lbp_value_quotients, texture_entropy = extract_rough_features_1(lbp_image, defect_polygon)
                lengthy_quotient = extract_lengthy_feature(lengthy_image, defect_polygon)
                number_lengthy_objects, avg_aspect_ratio, rel_length = extract_lengthy_features_1(edges_for_lengthy_feature, defect_polygon)
                #circle_existence = extract_circle_feature(image, circles, defect_polygon)
                in_shape_quotient = extract_in_shape_feature(convex_shapes_image, defect_polygon)
                roundness_value = extract_roundness_feature(convex_shapes_image, hulls, defect_polygon) 
                hu_moments = extract_hu_moments_features(convex_shapes_image, contours, defect_polygon) 

                temp_dict = {'image_number': i, 'defect_number': k, 'label': label,
                            'darker': darker_quotient, 'gradient': gradient_feature, 'reddish': reddish_quotient, 'metallic': metallic_quotient, 
                            'colorful': colorful_quotient,
                            'black': black_quotient, 'black_thin': black_thin_proportion, "dominating_color": dominating_color, 
                            'color_bin_1': color_bin_quotients[0], 'color_bin_2': color_bin_quotients[1],'color_bin_3': color_bin_quotients[2],
                            'color_bin_4': color_bin_quotients[3], 'color_bin_5': color_bin_quotients[4], 'color_bin_6': color_bin_quotients[5],
                            'color_bin_7': color_bin_quotients[6], 'color_bin_8': color_bin_quotients[7], 'color_bin_9': color_bin_quotients[8],
                            "color_entropy": color_entropy,
                            'rough': rough_quotient, 'dominating_texture': dominating_texture, 'texture_0': lbp_value_quotients[0], 
                            'texture_1': lbp_value_quotients[1], 'texture_2': lbp_value_quotients[2], 'texture_3': lbp_value_quotients[3], 
                            'texture_4': lbp_value_quotients[4], 'texture_5': lbp_value_quotients[5], 'texture_6': lbp_value_quotients[6], 
                            'texture_7': lbp_value_quotients[7], 'texture_8': lbp_value_quotients[8], 'texture_9': lbp_value_quotients[9], 
                            'rough_entropy': texture_entropy,
                            'lengthy': lengthy_quotient, 'number_lengthy_objects': number_lengthy_objects, 'lengthy_aspect_ratio': avg_aspect_ratio, 
                            'rel_length': rel_length, 'in_shape': in_shape_quotient, 'roundness': roundness_value,
                            'hu_moment_1': hu_moments[0], 'hu_moment_2': hu_moments[1], 'hu_moment_3': hu_moments[2], 'hu_moment_4': hu_moments[3],
                            'hu_moment_5': hu_moments[4], 'hu_moment_6': hu_moments[5], 'hu_moment_7': hu_moments[6]}
                samples.append(temp_dict)
            except:
                pass

samples = pd.DataFrame(samples)
samples.to_csv(f"samples_{start}_{end}_all_defects.csv")


#Anpassen der feature-extraction für random forest training und parameter tuning
# -> finde features für n mal den gewünschten Defekt, danach n mal einen beliebigen anderen Defekt


Processing image 0000


C:\Users\koeni\AppData\Local\Temp\ipykernel_31412\868888855.py:25: DeprecationWarning: `np.int0` is a deprecated alias for `np.intp`.  (Deprecated NumPy 1.24)
  box = np.int0(box)
C:\Users\koeni\AppData\Local\Temp\ipykernel_31412\2386869206.py:55: DeprecationWarning: `np.int0` is a deprecated alias for `np.intp`.  (Deprecated NumPy 1.24)
  box = np.int0(box)



Processing image 0010

Processing image 0020

Processing image 0030

Processing image 0040

Processing image 0050


c:\Users\koeni\Documents\Programme\Python_3.11\Lib\site-packages\numpy\core\fromnumeric.py:3464: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
c:\Users\koeni\Documents\Programme\Python_3.11\Lib\site-packages\numpy\core\_methods.py:192: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)



Processing image 0060

Processing image 0070

Processing image 0080

Processing image 0090

Processing image 0100

Processing image 0110

Processing image 0120

Processing image 0130

Processing image 0140

Processing image 0150

Processing image 0160

Processing image 0170

Processing image 0180

Processing image 0190

Processing image 0200

Processing image 0210

Processing image 0220

Processing image 0230

Processing image 0240

Processing image 0250

Processing image 0260

Processing image 0270

Processing image 0280

Processing image 0290

Processing image 0300

Processing image 0310

Processing image 0320

Processing image 0330

Processing image 0340

Processing image 0350

Processing image 0360

Processing image 0370

Processing image 0380

Processing image 0390

Processing image 0400

Processing image 0410

Processing image 0420

Processing image 0430

Processing image 0440

Processing image 0450

Processing image 0460

Processing image 0470

Processing image 0480

Processing

In [55]:
samples = pd.read_csv("samples_0_6935.csv", sep = ",")

In [53]:
graffiti = samples[samples['label'] == 'Graffiti']
rust = samples[samples['label'] == 'Rust']
drainage = samples[samples['label'] == 'Drainage']
wetspot = samples[samples['label'] == 'Wetspot']
exposedrebars = samples[samples['label'] == 'ExposedRebars']
crack = samples[samples['label'] == 'Crack']

print("Grafitti:")
print(graffiti.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))
print()

print("Rust:")
print(rust.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))
print()

print("Drainage:")
print(drainage.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))
print()

print("Wetspot:")
print(wetspot.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))
print()

print("ExposedRebars:")
print(exposedrebars.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))
print()

print("Crack:")
print(crack.loc[:,["darker", "gradient", "reddish", "metallic", "colorful", "black", "black_thin", "dominating_color", "color_bin_1", "color_bin_2", 
                      "color_bin_3", "color_bin_4", "color_bin_5", "color_bin_6", "color_bin_7", "color_bin_8", "color_bin_9", "color_entropy", 
                      "rough", "dominating_texture", "texture_0", "texture_1", "texture_2", "texture_3", "texture_4", "texture_5", "texture_6", 
                      "texture_7", "texture_8", "texture_9", "rough_entropy", "lengthy", "number_lengthy_objects", "lengthy_aspect_ratio", "rel_length", 
                      "in_shape", "roundness", "hu_moment_1", "hu_moment_2", "hu_moment_3", "hu_moment_4", "hu_moment_5", "hu_moment_6", 
                      "hu_moment_7"]].mean(axis = 0))



Grafitti:
darker                       0.241339
gradient                     0.980432
reddish                      0.110030
metallic                     0.224878
colorful                     0.252387
black                        0.064420
black_thin                   0.082137
dominating_color             3.762766
color_bin_1                  0.232982
color_bin_2                  0.217040
color_bin_3                  0.055612
color_bin_4                  0.047980
color_bin_5                  0.089489
color_bin_6                  0.202161
color_bin_7                  0.061502
color_bin_8                  0.023915
color_bin_9                  0.069318
color_entropy                1.554593
rough                        0.203825
dominating_texture           7.114362
texture_0                    0.063467
texture_1                    0.076134
texture_2                    0.059407
texture_3                    0.093198
texture_4                    0.163843
texture_5                    0.112759
te